In [1]:
#1. importing libraries
import pandas as pd
import re

In [2]:
#2. Loading Tweet Text from corresponding training and test files
path11="C://Users//FurqanSaddozai//scrapping_tweets_16_july_2022//Uni-multi-urdu-HS//"
file_path_1 = path11+"MMHS11K_train.xlsx"
file_path_2 = path11+"MMHS11K_test.xlsx"

# Load specific columns into a DataFrame
columns_to_load = ["Text", "Label"]
df_train = pd.read_excel(file_path_1, usecols=columns_to_load)
df_test = pd.read_excel(file_path_2, usecols=columns_to_load)

# Display the DataFrame
print('Training data')
print(df_train[:3])
print('................................')
print('Test data')
print(df_test[:3])

Training data
                                                Text    Label
0  مرد کی بہت سی پریشانیاں خوبصورت عورت کو دیکھ ک...  No_Hate
1  یورپی ممالک کو گیس اور بجلی کی قلت کے باعث موس...  No_Hate
2  نائب صدر مسلم لیگ ن پنجاب رانا مشہود احمد خاں ...  No_Hate
................................
Test data
                                                Text Label
0  @SdqJaan اس مادر چوت کی مسخ شدہ لاش ملنی چائیے...  Hate
1  @Jooookeeeerrrr یہ کس گانڈو کی اولاد ہے؟جو 60 ...  Hate
2  @ihsannaseem1 ایسی لوگ ہوتے ہیں بہن فروش ، شکل...  Hate


In [3]:
#3. printing number of samples in training and test files
print(len(df_train))
print(len(df_test))

8800
2200


In [4]:
# 4. Text Preprocessing: All usernames, extra white spaces,URLs, digits, emojis, English characters & words,
#special characters, diacritics & punctutations are removed. Moreover, Text is tokenizedv into words   
# Removing all digits, non-Urdu characters or words from Tweet text
df_train['Text']=df_train['Text'].apply((lambda x: re.sub(r'[^\u0600-\u06FF\s]+',' ',x)))
df_test['Text']=df_test['Text'].apply((lambda x: re.sub(r'[^\u0600-\u06FF\s]+',' ',x)))

# Removing all Urdu digits  from Tweet text
df_train['Text']=df_train['Text'].apply((lambda x: re.sub('[۰-۹]',' ',x)))
df_test['Text']=df_test['Text'].apply((lambda x: re.sub('[۰-۹]',' ',x)))

#Removing all punctuations marks from tweets text
df_train['Text']=df_train['Text'].apply((lambda x: re.sub('[^\w\s]',' ',x)))
df_test['Text']=df_test['Text'].apply((lambda x: re.sub('[^\w\s]',' ',x)))

#Replace '_' with white space
df_train['Text']=df_train['Text'].apply((lambda x: re.sub('_',' ',x)))
df_test['Text']=df_test['Text'].apply((lambda x: re.sub('_',' ',x)))

#Tokenization using NLTK
import nltk
def identify_tokens(row):
    text= row['Text'] 
    #print(poem)# output is entire poem text
    tokens = nltk.word_tokenize(text)
    #print('tokens of poem are')
    #print(tokens)
    #aa=input("need more?")
    return tokens
df_train['Text'] = df_train.apply(identify_tokens, axis=1)# apply method has axis column showing:
df_test['Text'] = df_test.apply(identify_tokens, axis=1)# apply method has axis column showing:

#Removing stopwords and characters having lenggth<=1 from tweet text
#Importing manually compiled Urdu stopwords list having 414 entries
urdu_stop_word_file='C:\\Users\\FurqanSaddozai\\scrapping_tweets_16_july_2022\\Uni-multi-urdu-HS\\DFF_2023\\Urdu_stopwords.txt'
import codecs
f=codecs.open(urdu_stop_word_file,'r','utf-8-sig')
text=f.read()
stops=text.split()
f.close()

#Removing stopwords and single characters from Text
def remove_stops(row):
    my_list = row['Text']
    meaningful_words1 = [w for w in my_list if not w in stops]
    meaningful_words2 = [w for w in meaningful_words1 if len(w)>1]
    return (meaningful_words2)

df_train['Text'] = df_train.apply(remove_stops, axis=1)# apply method has axis column showing:
df_test['Text'] = df_test.apply(remove_stops, axis=1)# apply method has axis column showing:

#Rejoining tokenized words into strings/text
def rejoin_words(row):
    my_list = row['Text']
    joined_words = ( " ".join(my_list))
    return joined_words

df_train['Text'] = df_train.apply(rejoin_words, axis=1)# apply method has axis column showing:
df_test['Text'] = df_test.apply(rejoin_words, axis=1)# apply method has axis column showing:

In [5]:
#5. Dividing training and test dataframes into corresponding variables: X_train, X_test, y_train, y_test
X_train=df_train['Text']
X_test=df_test['Text']
y_train=df_train['Label']
y_test=df_test['Label']

In [6]:
#6. Converting labels into numerical values
from tensorflow.keras.utils import to_categorical
# Convert labels to numerical values
labels1 = y_train.map({'Hate': 1, 'No_Hate': 0})
labels1 = to_categorical(labels1)  # Convert to one-hot encoded format
labels2 = y_test.map({'Hate': 1, 'No_Hate': 0})
labels2 = to_categorical(labels2)  # Convert to one-hot encoded format
y_train=labels1
y_test=labels2

In [7]:
#7. Tokenize text, converting it into sequence of integers, and padding the sequences
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

#X_train.shape
max_features = 5300
max_len=50  # here 54 is the number of words in longest training tweet text
tokenizer = Tokenizer(num_words=max_features, split=' ')
tokenizer.fit_on_texts(X_train.values)
X1 = tokenizer.texts_to_sequences(X_train.values)
X1 = pad_sequences(X1,maxlen=max_len)

#tokenizer.fit_on_texts(X_test.values)
X2 = tokenizer.texts_to_sequences(X_test.values)
X2 = pad_sequences(X2,maxlen=max_len)

In [8]:
#8. Presenting the shape of input features and target variables/labels
print(X1.shape)
print(X2.shape)
print(y_train.shape)
print(y_test.shape)

(8800, 50)
(2200, 50)
(8800, 2)
(2200, 2)


In [9]:
#9. Finding the total length of vocabulary
vocab_size = len(tokenizer.word_index) + 1

In [10]:
#10. Printing the total length of vocabulary
print(vocab_size)

21512


In [11]:
#11. Load pre-trained word embeddings (specifically skipgram embeddings) for Urdu language.
#we downloaded skipgram embeddings from link
##https://github.com/samarh/urduvec

from gensim.models import word2vec
model = word2vec.KeyedVectors.load_word2vec_format('urduvec_140M_100K_300d.bin', binary=True)

In [12]:
#12. Create an embedding matrix for words in the tokenizer's vocabulary using pre-trained word embeddings
#only selected first 80 embeddings from 300 embeddings
import numpy as np

embedding_dim = 300  # Adjust based on your pretrained embedding dimension
selected_embedding_dim = 80  # Number of dimensions to select
num_words = len(tokenizer.word_index) + 1
embedding_matrix = np.zeros((num_words, selected_embedding_dim))  # Use selected_embedding_dim

for word, index in tokenizer.word_index.items():
    if word in model:
        full_embedding = model[word]  # Assuming model[word] gives you a 300-dimensional embedding
        selected_embedding = full_embedding[:selected_embedding_dim]  # Extract first 50 dimensions
        embedding_matrix[index] = selected_embedding

In [13]:
#13. Define and compile a Bidirectional LSTM neural network model for binary classification using Keras
from keras.models import Sequential
from keras.layers import Embedding, LSTM, Flatten, Dropout, Dense, Bidirectional
from keras.optimizers import Adam
import tensorflow as tf

# Set random seeds for reproducibility
seed_value = 10
np.random.seed(seed_value)
tf.random.set_seed(seed_value)
model = Sequential()
embedding_dim=80 #output embedding dimensions
model.add(Embedding(vocab_size, embedding_dim, weights=[embedding_matrix], input_length=max_len, trainable=False))
# Add an BiLSTM layer with 150 units
model.add(Bidirectional(LSTM(150, return_sequences = False, activation='relu')))
#Dense layer
model.add(Dense(512, activation='relu'))
#Dropout layer 
model.add(Dropout(0.5))
#Classification Layer
model.add(Dense(2, activation='sigmoid'))

#model.summary()
learning_rate = 0.001
optimizer = Adam(learning_rate=learning_rate)

model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['accuracy'])

In [14]:
#14. Model summary
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, 50, 80)            1720960   
                                                                 
 bidirectional (Bidirection  (None, 300)               277200    
 al)                                                             
                                                                 
 dense (Dense)               (None, 512)               154112    
                                                                 
 dropout (Dropout)           (None, 512)               0         
                                                                 
 dense_1 (Dense)             (None, 2)                 1026      
                                                                 
Total params: 2153298 (8.21 MB)
Trainable params: 432338 (1.65 MB)
Non-trainable params: 1720960 (6.56 MB)
_______________

In [15]:
#15. Train a neural network model while monitoring the validation loss and stopping the training process 
#early if the validation loss does not improve for a specified number of epochs.
from tensorflow.keras.callbacks import EarlyStopping

# Define the EarlyStopping callback
early_stopping = EarlyStopping(monitor='val_loss', patience=2, restore_best_weights=True)
#Training model
model.fit(X1, y_train, epochs=20, batch_size=128, validation_data=(X2, y_test), callbacks=[early_stopping])

Epoch 1/20
69/69 [==============================] - 21s 237ms/step - loss: 0.7062 - accuracy: 0.5057 - val_loss: 0.6923 - val_accuracy: 0.5532
Epoch 2/20
69/69 [==============================] - 15s 224ms/step - loss: 0.7010 - accuracy: 0.5043 - val_loss: 0.7134 - val_accuracy: 0.5000
Epoch 3/20
69/69 [==============================] - 15s 224ms/step - loss: 0.7022 - accuracy: 0.5155 - val_loss: 0.7151 - val_accuracy: 0.5000
Epoch 4/20
69/69 [==============================] - 15s 225ms/step - loss: 0.7137 - accuracy: 0.5030 - val_loss: 0.7049 - val_accuracy: 0.5000


In [16]:
#16. Finding & printing Test accuracy & loss
test_loss, test_accuracy = model.evaluate(X2, y_test, batch_size=128)
print(test_accuracy)
print(test_loss)

18/18 [==============================] - 2s 83ms/step - loss: 0.6923 - accuracy: 0.5532
0.5541818270683289
0.5532605633735657


In [17]:
#https://machinelearningmastery.com/how-to-calculate-precision-recall-f1-and-more-for-deep-learning-models/
from sklearn.datasets import make_circles
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import f1_score
from sklearn.metrics import cohen_kappa_score
from sklearn.metrics import roc_auc_score
from sklearn.metrics import confusion_matrix

In [18]:
#First, we must use the model to make predictions. 
#Most of the metric functions require a comparison between the true class values (e.g. testy) and 
#the predicted class values (yhat_classes). 

#We can predict the class values directly with our model using the predict_classes() function on the model.
#Some metrics, like the ROC AUC, require a prediction of class probabilities (yhat_probs). 
#These can be retrieved by calling the predict() function on the model.

# predict probabilities for test set
#yhat_probs = model.predict(X2, verbose=0)
# predict crisp classes for test set
#yhat_classes = model.predict_classes(X2, verbose=0)
yhat_classes = (model.predict(X2) > 0.5).astype("int32")#taken from 
#https://discuss.tensorflow.org/t/sequential-object-has-no-attribute-predict-classes/10157/5
#as (yhat_classes = model.predict_classes(X2, verbose=0))was giving error

69/69 [==============================] - 3s 31ms/step


In [19]:
#yhat_classes[0]

In [20]:
yhat_classes = yhat_classes[:, 0]
y_test=y_test[:, 0]

In [21]:
#yhat_classes[0]

In [22]:
#y_test[0]

In [23]:
#We are now ready to calculate metrics for our deep learning neural network model. 
#We can start by calculating the classification accuracy, precision, recall, and F1 scores.

# accuracy: (tp + tn) / (p + n)
accuracy = accuracy_score(y_test, yhat_classes)
print('Accuracy: %f' % accuracy)
# precision tp / (tp + fp)
precision = precision_score(y_test, yhat_classes)
print('Precision: %f' % precision)
# recall: tp / (tp + fn)
recall = recall_score(y_test, yhat_classes)
print('Recall: %f' % recall)
# f1: 2 tp / (2 tp + fp + fn)
f1 = f1_score(y_test, yhat_classes)
print('F1 score: %f' % f1)

Accuracy: 0.554091
Precision: 0.534334
Recall: 0.841818
F1 score: 0.653724
